In [1]:
# Basics
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np

# Plotly
import plotly.graph_objects as go
import plotly.figure_factory as ff
import plotly.express as px
from plotly.subplots import make_subplots


# Tools
from copy import copy # Shallow copy
from itertools import product
from collections import defaultdict
from functools import partial
from IPython.display import display # Allows functions to simultaneously return values and show tables

# Styling
from colorama import Fore
from colorama import Style
from matplotlib.colors import Colormap


# Assessing Feature Importance
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.feature_selection import mutual_info_classif

# Pipeline
from sklearn.pipeline import make_pipeline
#from sklearn.preprocessing import Binarizer
#from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import StandardScaler, PowerTransformer, OneHotEncoder, FunctionTransformer
from sklearn.compose import make_column_selector, make_column_transformer






from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.model_selection import StratifiedKFold, RandomizedSearchCV

from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC


from sklearn.metrics import accuracy_score



# t-SNE
from sklearn.manifold import TSNE


# Dendogram
from scipy.cluster.hierarchy import linkage
from scipy.spatial.distance import squareform


# Kde Plots
from scipy.stats import gaussian_kde



# Probability plots
from scipy.stats import probplot

# The Tree Trio
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier


import scipy.stats as stats

# Good ol utils
from utils import *

# Sequential Feature Selection
from mlxtend.feature_selection import SequentialFeatureSelector as SFS
from mlxtend.plotting import plot_sequential_feature_selection as plot_sfs

In [2]:
train = pd.read_csv(r"C:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\data\train.csv", index_col="id").rename(columns=str.strip)
test = pd.read_csv(r"C:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\data\test.csv", index_col="id").rename(columns=str.strip)

target = "Target"

value_mapping = {
    'Enrolled': 2,
    'Dropout': 0,
    'Graduate': 1
}

# Replace the values in the "Target" column
train['Target'] = train['Target'].replace(value_mapping)



In [3]:
BINARY_COLUMNS = []
for column in train.columns:
    if len(train[column].value_counts()) == 2:
        BINARY_COLUMNS.append(column)

binary_data = train[BINARY_COLUMNS+ ['Target']]



ONE_HOT_COLUMNS = ['Marital status', 
                   'Application order', 
                   'Application mode', 
                   'Course', 
                   'Previous qualification', 
                   'Nacionality', 
                   'Mother\'s qualification', 
                   'Father\'s qualification', 
                   'Mother\'s occupation', 
                   'Father\'s occupation']

one_hot_data = train[ONE_HOT_COLUMNS + ['Target']]




NUMERIC_COLUMNS = train.drop(columns = ONE_HOT_COLUMNS + BINARY_COLUMNS + ['Target']).columns.to_list()
numeric_data = train[NUMERIC_COLUMNS + ['Target']]



FLOAT_COLUMNS = train[NUMERIC_COLUMNS].select_dtypes('float').columns.to_list()
float_data = train[FLOAT_COLUMNS + ['Target']]



INTEGER_COLUMNS = train[NUMERIC_COLUMNS].select_dtypes('int').columns.to_list()
integer_data = train[INTEGER_COLUMNS + ['Target']]




BINARY_INDICATOR_FEATURES = ['Curricular units 2nd sem (without evaluations)',
                             'Curricular units 2nd sem (grade)',
                             'Curricular units 2nd sem (approved)',
                             'Curricular units 2nd sem (evaluations)',
                             'Curricular units 2nd sem (credited)',
                             'Curricular units 1st sem (without evaluations)',
                             'Curricular units 1st sem (grade)',
                             'Curricular units 1st sem (approved)',
                             'Curricular units 1st sem (evaluations)',
                             'Curricular units 1st sem (credited)',
]

In [4]:
positive_features = list(numeric_data[NUMERIC_COLUMNS].describe().T.query("min > 0").index)
zero_features = list(numeric_data[NUMERIC_COLUMNS].describe().T.query("min == 0").index)
negative_features = list(numeric_data[NUMERIC_COLUMNS].describe().T.query("min < 0").index)

In [5]:
epsilon = 0.0001
GDP_shift = 4.0601
Inflation_shift = 0.8001
r2_scores = defaultdict(tuple)

for feature in NUMERIC_COLUMNS:
    orig = numeric_data.sample(5000)[feature].dropna()
    if feature in positive_features:
        _, (*_, R_orig) = probplot(orig, rvalue=True)
        _, (*_, R_log1p) = probplot(np.log1p(orig), rvalue=True)
        _, (*_, R_square) = probplot(np.square(orig), rvalue=True)
        _, (*_, R_yeojohn) = probplot(stats.yeojohnson(orig)[0], rvalue=True)
    elif feature in zero_features:
        _, (*_, R_orig) = probplot(orig, rvalue=True)
        _, (*_, R_log1p) = probplot(np.log1p(orig), rvalue=True)
        _, (*_, R_square) = probplot(np.square(orig), rvalue=True)
        _, (*_, R_yeojohn) = probplot(stats.yeojohnson(orig)[0], rvalue=True)
    elif feature == 'GDP':
        _, (*_, R_orig) = probplot(orig, rvalue=True)
        _, (*_, R_log1p) = probplot(np.log1p(orig + GDP_shift), rvalue=True)
        _, (*_, R_square) = probplot(np.square(orig + GDP_shift), rvalue=True)
        _, (*_, R_yeojohn) = probplot(stats.yeojohnson(orig)[0], rvalue=True)
    elif feature == 'Inflation Rate':
        _, (*_, R_orig) = probplot(orig, rvalue=True)
        _, (*_, R_log1p) = probplot(np.log1p(orig + Inflation_shift), rvalue=True)
        _, (*_, R_square) = probplot(np.square(orig + Inflation_shift), rvalue=True)
        _, (*_, R_yeojohn) = probplot(stats.yeojohnson(orig)[0], rvalue=True)

    r2_scores[feature] = (
        R_orig * R_orig,
        R_log1p * R_log1p,
        R_square * R_square,
        R_yeojohn * R_yeojohn
    )

r2_scores = pd.DataFrame(
    r2_scores, index=("Original", "Log1p", "Square", "YeoJohnson")
).T

r2_scores["HighestScore"] = r2_scores[["Original", "Log1p", "Square", "YeoJohnson"]].max(axis = 1)
r2_scores["Winner"] = r2_scores.idxmax(axis=1)


def highlight_max(s):
    is_max = s == s.max()
    return [f'background-color: {TEAL}' if v else '' for v in is_max]

r2_scores['Improvement'] = r2_scores['HighestScore'] - r2_scores['Original']
r2_scores.style.set_table_styles(DF_STYLE).apply(highlight_max, subset= ["Original", "Log1p", "Square", "YeoJohnson"], axis=1).background_gradient(cmap = DF_CMAP2, subset = 'Improvement').format(precision = 3)

In [6]:
square_transform_cols = r2_scores.query("Winner == 'Square'").index
yeojohnson_transform_cols = r2_scores.query("Winner == 'YeoJohnson' & Improvement >= 0.05").index
no_transform_cols = r2_scores.query("Improvement < 0.05").index


square_transform_cols = [
    'Curricular units 2nd sem (grade)',
    'Curricular units 1st sem (grade)'
]

yeojohnson_transform_cols = ['Age at enrollment']

no_transform_cols = [
        'Previous qualification (grade)', 'Admission grade',
        'Curricular units 1st sem (credited)',
        'Curricular units 1st sem (enrolled)',
        'Curricular units 1st sem (evaluations)',
        'Curricular units 1st sem (approved)',
        'Curricular units 1st sem (without evaluations)',
        'Curricular units 2nd sem (credited)',
        'Curricular units 2nd sem (enrolled)',
        'Curricular units 2nd sem (evaluations)',
        'Curricular units 2nd sem (approved)',
        'Curricular units 2nd sem (without evaluations)', 'Unemployment rate',
        'Inflation rate', 'GDP'
]






In [28]:
no_transform_cols

Index(['Previous qualification (grade)', 'Admission grade',
       'Curricular units 1st sem (credited)',
       'Curricular units 1st sem (enrolled)',
       'Curricular units 1st sem (evaluations)',
       'Curricular units 1st sem (approved)',
       'Curricular units 1st sem (without evaluations)',
       'Curricular units 2nd sem (credited)',
       'Curricular units 2nd sem (enrolled)',
       'Curricular units 2nd sem (evaluations)',
       'Curricular units 2nd sem (approved)',
       'Curricular units 2nd sem (without evaluations)', 'Unemployment rate',
       'Inflation rate', 'GDP'],
      dtype='object')

In [7]:
initial_preprocess = make_pipeline(
        make_column_transformer(
        (
            StandardScaler(),
            no_transform_cols.to_list(),  # Columns not requiring transformation
        ),
        (
            make_pipeline(
                FunctionTransformer(func=np.square, feature_names_out="one-to-one"),#, validate=False),
                StandardScaler(),
            ),
            square_transform_cols.to_list(),  # Columns to be squared and then scaled
        ),
        (
            PowerTransformer(method="yeo-johnson", standardize=True),
            yeojohnson_transform_cols.to_list(),  # Columns to be transformed using Yeo-Johnson
        ),
        #(
        #    OneHotEncoder(sparse_output = False, handle_unknown = "use_encoded_value", unknown_value=-1),
        #    ONE_HOT_COLUMNS,  # Columns to be one-hot encoded
        #),
        remainder="passthrough",  # Pass through columns not specified above
        verbose_feature_names_out=False,
    ),
)




In [8]:
X = train.drop(target, axis=1)
y = train[target]


# Simply checking our pipeline is working properly
X_processed = initial_preprocess.fit_transform(X)
X_processed_frame = pd.DataFrame(X_processed, columns=initial_preprocess.get_feature_names_out(), index=X.index)
X_processed_frame.head().style.set_table_styles(DF_STYLE).format(precision=3)

In [9]:
X_processed.shape[1]
X_processed_frame.shape

(76518, 36)

# Impurity Feature Importance

In [15]:
n_bags = 10
n_folds = 5
np.random.seed(42)
seeds = np.random.randint(0, 19937, size=n_bags)

classifiers = ['rf', 'cat', 'lgbm', 'xgb']
forest_info_average = np.zeros(X_processed.shape[1]) #36 features
cat_info_average = np.zeros(X_processed.shape[1])
lgbm_info_average = np.zeros(X_processed.shape[1])
xgb_info_average = np.zeros(X_processed.shape[1])

for selected_classifier in classifiers:
    for seed in seeds:
        skfold = StratifiedKFold(n_splits=n_folds, shuffle=True, random_state=seed)

        for train_ids, valid_ids in skfold.split(X, y):
            X_train, y_train = X.iloc[train_ids], y.iloc[train_ids]
            X_valid, y_valid = X.iloc[valid_ids], y.iloc[valid_ids]

            X_train = initial_preprocess.fit_transform(X_train)
            X_valid = initial_preprocess.transform(X_valid)


        if selected_classifier == 'rf':
            classifier = RandomForestClassifier(class_weight="balanced", random_state = seed, n_jobs = -1, max_features = 1, max_depth= 9)
            classifier.fit(X_train, y_train)
            print(f"forest Train Accuracy: {accuracy_score(y_train, classifier.predict(X_train))}")
            print(f"forest Validation Accuracy: {accuracy_score(y_valid, classifier.predict(X_valid))}")
            forest_info = classifier.feature_importances_
            forest_info = forest_info / forest_info.sum()
            forest_info_average += forest_info


        elif selected_classifier == 'cat':
            classifier = CatBoostClassifier(random_state = seed, auto_class_weights= "Balanced", classes_count= 3, thread_count= -1, rsm = 1, verbose = 0, depth = 8, learning_rate = 0.02) #rsm is proportion of columns for each new tree
            classifier.fit(X_train, y_train)
            print(f"cat Train Accuracy: {accuracy_score(y_train, classifier.predict(X_train))}")
            print(f"cat Accuracy: {accuracy_score(y_valid, classifier.predict(X_valid))}")
            cat_info = classifier.feature_importances_
            cat_info = cat_info / cat_info.sum()
            cat_info_average += cat_info


        elif selected_classifier == 'lgbm':
            classifier = LGBMClassifier(random_state = seed, class_weight = 'balanced', n_jobs = -1, objective = 'multiclass', max_depth = 10, n_estimators= 100, verbose = 10, colsample_bytree= 1, reg_alpha = 1, reg_lambda = 1, learning_rate = 0.02)
            classifier.fit(X_train, y_train)
            print(f"lgbm Train Accuracy: {accuracy_score(y_train, classifier.predict(X_train))}")
            print(f"lgbm Accuracy: {accuracy_score(y_valid, classifier.predict(X_valid))}")
            lgbm_info = classifier.feature_importances_
            lgbm_info = lgbm_info / lgbm_info.sum()
            lgbm_info_average += lgbm_info


        elif selected_classifier == 'xgb':
            classifier = XGBClassifier(random_state=seed, n_jobs = -1, objective = 'multiclass', max_depth = 5, n_estimators= 100, reg_alpha = 2, colsample_bytree = 0.9, reg_lambda = 1, learning_rate = 0.02)
            classifier.fit(X_train, y_train)
            print(f"xgb Train Accuracy: {accuracy_score(y_train, classifier.predict(X_train))}")
            print(f"xgb Accuracy: {accuracy_score(y_valid, classifier.predict(X_valid))}")
            xgb_info = classifier.feature_importances_
            xgb_info = xgb_info / xgb_info.sum()
            xgb_info_average += xgb_info

    forest_info_average = forest_info_average/n_bags/n_folds
    cat_info_average = cat_info_average/n_bags/n_folds
    lgbm_info_average = lgbm_info_average/n_bags/n_folds
    xgb_info_average = xgb_info_average/n_bags/n_folds
            
importances = pd.DataFrame(
    [forest_info, cat_info, lgbm_info, xgb_info],
    columns=initial_preprocess.get_feature_names_out(),
    index=["FOREST", "CAT","LGBM", "XGB"],
).T


importance_score_summary = importances.T.describe().T.sort_values(by = 'mean', ascending = False)
importance_score_summary['impor_score'] = range(1, len(importance_score_summary) + 1)
importance_score_summary[['impor_score', 'min', 'max', 'mean']].style.set_table_styles(DF_STYLE).background_gradient(
                                                                        cmap = DF_CMAP2, 
                                                                        subset = ['mean'], 
                                                                        vmin = importance_score_summary['mean'].min(),
                                                                        vmax = importance_score_summary['mean'].mean(),
                                                            ).background_gradient(
                                                                        cmap = DF_CMAP, 
                                                                        subset = 'min', 
                                                                        vmin = importance_score_summary['min'].min(),
                                                                        vmax = importance_score_summary['min'].mean(),
                                                            ).background_gradient(
                                                                        cmap = DF_CMAP, 
                                                                        subset = 'max', 
                                                                        vmin = importance_score_summary['max'].min(),
                                                                        vmax = importance_score_summary['max'].mean(),
                                                                        
                                                            ).format(precision = 3)

forest Train Accuracy: 0.7942987829780283
forest Validation Accuracy: 0.7899758217343005
forest Train Accuracy: 0.7894306950910724
forest Validation Accuracy: 0.7869698751878716
forest Train Accuracy: 0.7925671812464266
forest Validation Accuracy: 0.7852708619224988
forest Train Accuracy: 0.7966021399983664
forest Validation Accuracy: 0.7888649284454029
forest Train Accuracy: 0.7937270276892918
forest Validation Accuracy: 0.7863817552113964
forest Train Accuracy: 0.7939230580740014
forest Validation Accuracy: 0.7903679017186173
forest Train Accuracy: 0.7967491627868987
forest Validation Accuracy: 0.7917401816637261
forest Train Accuracy: 0.7923711508617169
forest Validation Accuracy: 0.7840946219695485
forest Train Accuracy: 0.7940210732663563
forest Validation Accuracy: 0.7850748219303405
forest Train Accuracy: 0.7931716082659479
forest Validation Accuracy: 0.7879500751486637
cat Train Accuracy: 0.8345176835742874
cat Accuracy: 0.8231719270731229
cat Train Accuracy: 0.8339622641509434

In [16]:
importances_melted_frame = (
    importances.melt(
        var_name="Method",
        value_name="Importance",
        ignore_index=False,
    )
    .reset_index()
    .rename(columns={"index": "Feature"})
    .round(4)
)

fig = px.bar(
    importances_melted_frame,
    x="Importance",
    y="Feature",
    color="Importance",
    facet_col="Method",
    facet_col_spacing=0.07,
    height=2000,
    width=1800,
    color_continuous_scale=color_map,
    title="Normalised Feature Importances (Three Different Default Methods)",
)
fig.update_annotations(font_size=20)
fig.update_yaxes(
    matches=None,
    showticklabels=True,
    categoryorder="total ascending",
    tickfont_size=15,
)
fig.update_xaxes(matches=None)
fig.update_traces(width=0.7)
fig.update_layout(
    font_color=FONT_COLOR,
    title_font_size=25,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    coloraxis_colorbar=dict(
        orientation="h",
        title_side="bottom",
        yanchor="bottom",
        xanchor="center",
        title=None,
        y=-0.05,
        x=0.5,
    ),
)
fig.show()

# Permutation Feature Importance

In [12]:
from sklearn.metrics import log_loss, roc_auc_score, brier_score_loss, average_precision_score
import numpy as np
import pandas as pd
from collections import defaultdict
from functools import partial
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC
from lightgbm import LGBMClassifier
from sklearn.model_selection import StratifiedKFold

# Defines the metric function to be used. Note: We're calculating the probability values of each class, not the target predictions, hence we can't use metrics like accuracy. 
def evaluation_metric(y_true, y_pred_proba, metric='log loss'):
    """Evaluates the chosen metric."""
    if metric == 'log loss':
        return log_loss(y_true, y_pred_proba)
    elif metric == 'roc auc':
        return roc_auc_score(y_true, y_pred_proba, multi_class='ovr')
    elif metric == 'brier':
        return brier_score_loss(y_true, y_pred_proba[:, 1]) # Brier is only for binary, not applicable here
    elif metric == 'average precision':
        return average_precision_score(y_true, y_pred_proba, average='micro')
    else:
        raise ValueError("Unsupported metric provided.")

n_bags = 5
n_folds = 5
metric = 'log loss'  # Change this to 'roc_auc', 'brier', or 'average_precision' depending on what metric you want to use

np.random.seed(42)
seeds = np.random.randint(0, 19937, size=n_bags)
original_scores = []
permutation_scores = pd.DataFrame()

# No longer needed
#forest = RandomForestClassifier(class_weight="balanced", random_state=42, n_jobs = -1)
#cat = CatBoostClassifier(random_state = 42, auto_class_weights= "Balanced", classes_count= 3, thread_count= -1)
#lgbm = LGBMClassifier(random_state=42, class_weight = 'balanced', n_jobs = -1, objective = 'multiclass', max_depth = 15, n_estimators= 1000, verbose = 10)


classifiers = ['rf', 'cat', 'lgbm', 'xgb']

for selected_classifier in classifiers:
    y_proba_original = np.zeros((len(y), len(np.unique(y))), dtype=np.float64)
    y_proba_shuffled = defaultdict(partial(np.zeros, (len(y), len(np.unique(y))), dtype=np.float64))



    for seed in seeds:
        skfold = StratifiedKFold(n_splits=n_folds, shuffle=True, random_state=seed)

        if selected_classifier == 'rf':
            classifier = RandomForestClassifier(class_weight="balanced", random_state = seed, n_jobs = -1)
        elif selected_classifier == 'cat':
            classifier = CatBoostClassifier(random_state = seed, auto_class_weights= "Balanced", classes_count= 3, thread_count= -1)
        elif selected_classifier == 'lgbm':
            classifier = LGBMClassifier(random_state = seed, class_weight = 'balanced', n_jobs = -1, objective = 'multiclass', max_depth = 10, n_estimators= 150, verbose = 0)
        elif selected_classifier == 'xgb':
            classifier = XGBClassifier(random_state=seed, n_jobs = -1, objective = 'multi:softmax', max_depth = 5, n_estimators= 150, reg_alpha = 2, colsample_bytree = 1)



        for train_ids, valid_ids in skfold.split(X, y):
            X_train, y_train = X.iloc[train_ids], y.iloc[train_ids]
            X_valid, y_valid = X.iloc[valid_ids], y.iloc[valid_ids]

            X_train = initial_preprocess.fit_transform(X_train)
            X_valid = initial_preprocess.transform(X_valid)

            classifier.fit(X_train, y_train)
            y_proba_original[valid_ids] += classifier.predict_proba(X_valid)

            for i, feature in enumerate(initial_preprocess.get_feature_names_out()):
                X_shuffled = X_valid.copy()
                X_shuffled[:, i] = np.random.permutation(X_shuffled[:, i])  # type: ignore
                y_proba_shuffled[feature][valid_ids] += classifier.predict_proba(X_shuffled)

    classifier_name = classifier.__class__.__name__
    feature_names = y_proba_shuffled.keys()
    print("step 1")
    original_scores.append(evaluation_metric(y, y_proba_original / n_bags, metric))
    print("step 2")
    permutation_scores[classifier_name] = pd.Series(
        [
            evaluation_metric(y, y_proba_shuffled[feature] / n_bags, metric)
            for feature in feature_names
        ],
        index=feature_names,
    )

# Display the results
print("Original scores:", original_scores)
print("Permutation scores:\n", permutation_scores)

step 1
step 2
Learning rate set to 0.097601
0:	learn: 1.0089153	total: 12.2ms	remaining: 12.2s
1:	learn: 0.9392323	total: 22.9ms	remaining: 11.4s
2:	learn: 0.8825449	total: 34.3ms	remaining: 11.4s
3:	learn: 0.8347275	total: 45.4ms	remaining: 11.3s
4:	learn: 0.7956245	total: 56.6ms	remaining: 11.3s
5:	learn: 0.7631348	total: 67.9ms	remaining: 11.2s
6:	learn: 0.7365848	total: 79ms	remaining: 11.2s
7:	learn: 0.7130836	total: 91.2ms	remaining: 11.3s
8:	learn: 0.6919683	total: 102ms	remaining: 11.2s
9:	learn: 0.6735217	total: 114ms	remaining: 11.3s
10:	learn: 0.6576310	total: 125ms	remaining: 11.3s
11:	learn: 0.6448943	total: 135ms	remaining: 11.1s
12:	learn: 0.6329680	total: 144ms	remaining: 10.9s
13:	learn: 0.6223174	total: 153ms	remaining: 10.8s
14:	learn: 0.6128619	total: 163ms	remaining: 10.7s
15:	learn: 0.6042609	total: 172ms	remaining: 10.6s
16:	learn: 0.5971216	total: 182ms	remaining: 10.5s
17:	learn: 0.5912730	total: 190ms	remaining: 10.4s
18:	learn: 0.5846901	total: 199ms	remainin

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\metrics\_classification.py:2981: UserWarning:

The y_pred values do not sum to one. Starting from 1.5 thiswill result in an error.

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\metrics\_classification.py:2981: UserWarning:

The y_pred values do not sum to one. Starting from 1.5 thiswill result in an error.

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\metrics\_classification.py:2981: UserWarning:

The y_pred values do not sum to one. Starting from 1.5 thiswill result in an error.

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\metrics\_classification.py:2981: UserWarning:

The y_pred values do not sum to one. Starting from 1.5 thiswill result in an error.

c:\Users\Nebula PC\D

Original scores: [0.4624877146864925, 0.4572249850892404, 0.4577092523079663, 0.43000617968770527]
Permutation scores:
                                                 RandomForestClassifier  \
Previous qualification (grade)                                0.460738   
Admission grade                                               0.458610   
Curricular units 1st sem (credited)                           0.462892   
Curricular units 1st sem (enrolled)                           0.463947   
Curricular units 1st sem (evaluations)                        0.466977   
Curricular units 1st sem (approved)                           0.520603   
Curricular units 1st sem (without evaluations)                0.463072   
Curricular units 2nd sem (credited)                           0.462006   
Curricular units 2nd sem (enrolled)                           0.466086   
Curricular units 2nd sem (evaluations)                        0.471523   
Curricular units 2nd sem (approved)                           0.64

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\metrics\_classification.py:2981: UserWarning:

The y_pred values do not sum to one. Starting from 1.5 thiswill result in an error.

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\metrics\_classification.py:2981: UserWarning:

The y_pred values do not sum to one. Starting from 1.5 thiswill result in an error.

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\metrics\_classification.py:2981: UserWarning:

The y_pred values do not sum to one. Starting from 1.5 thiswill result in an error.



In [13]:
permutation_score_summary = permutation_scores.T.describe().T.sort_values(by = 'mean', ascending = False)
permutation_score_summary['perm_score'] = range(1, len(permutation_score_summary) + 1)
permutation_score_summary[['perm_score', 'min', 'max', 'mean']].style.set_table_styles(DF_STYLE).background_gradient(
                                                                        cmap = DF_CMAP2, 
                                                                        subset = ['mean'], 
                                                                        vmin = permutation_score_summary['mean'].min(),
                                                                        vmax = permutation_score_summary['mean'].mean(),
                                                            ).background_gradient(
                                                                        cmap = DF_CMAP, 
                                                                        subset = 'min', 
                                                                        vmin = permutation_score_summary['min'].min(),
                                                                        vmax = permutation_score_summary['min'].mean(),
                                                            ).background_gradient(
                                                                        cmap = DF_CMAP, 
                                                                        subset = 'max', 
                                                                        vmin = permutation_score_summary['max'].min(),
                                                                        vmax = permutation_score_summary['max'].mean(),
                                                                        
                                                            ).format(precision = 3)

In [14]:
permutation_results_melted = (
    permutation_scores.melt(
        var_name="Method",
        value_name=f"{metric}",
        ignore_index=False,
    )
    .reset_index()
    .rename(columns={"index": "Feature"})
    .round(4)
)

fig = px.bar(
    permutation_results_melted,
    x=f"{metric}",
    y="Feature",
    color=f"{metric}",
    facet_col="Method",
    facet_col_spacing=0.07,
    height=2000,
    width=1800,
    color_continuous_scale=color_map,
    title=f"Permutation Test Results - {metric} when Permuting Samples"
    f"in Certain Features (Averaged over Stratified {n_folds}-Fold and {n_bags} Different Seeds)",
)
fig.update_annotations(font_size=15)
fig.update_traces(width=0.7)
fig.update_xaxes(matches=None)
fig.update_yaxes(
    matches=None,
    showticklabels=True,
    categoryorder="total ascending",
    tickfont_size=15,
)
fig.update_layout(
    font_color=FONT_COLOR,
    title_font_size=25,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    coloraxis_colorbar=dict(
        orientation="h",
        title_side="bottom",
        yanchor="bottom",
        xanchor="center",
        title=None,
        y=-0.2,
        x=0.5,
    ),
    margin_t=120,
)
for original_score, max_score, col in zip(
    original_scores, permutation_scores.max().tolist(), (1, 2, 3, 4)
):
    fig.add_vline(
        x=original_score,
        line_width=2,
        line_dash="dash",
        line_color= DARK_TEAL,
        col=col,
    )
    fig.add_vrect(
        x0=original_score,
        x1=max_score,
        line_width=0,
        fillcolor=DARK_TEAL,
        opacity=0.2,
        col=col,
    )
fig.show()

In [17]:
feature_rankings = importance_score_summary.join(permutation_score_summary, lsuffix='_impor', rsuffix='_perm')[['impor_score', 'perm_score']]
feature_rankings['average_score'] = feature_rankings[['impor_score', 'perm_score']].mean(axis=1)
feature_rankings.sort_values(by = 'average_score').style.set_table_styles(DF_STYLE).background_gradient(
                                                                       cmap = DF_CMAP2_R, 
                                                                       subset = ['impor_score'], 
                                                                       vmin = feature_rankings['impor_score'].min(),
                                                                       vmax = feature_rankings['impor_score'].mean(),
                                                                                    ).background_gradient(
                                                                       cmap = DF_CMAP2_R, 
                                                                       subset = ['perm_score'], 
                                                                       vmin = feature_rankings['perm_score'].min(),
                                                                       vmax = feature_rankings['perm_score'].mean(),
                                                                                    )

In [24]:
TOP_12_FEATURES_DF = feature_rankings.sort_values(by = 'average_score').iloc[0:11]
TOP_12_FEATURES_DF.to_csv('top_12_features.csv')


In [ ]:
BOTTOM_12_FEATURES_DF = feature_rankings.sort_values(by = 'average_score').iloc[0:11]
BOTTOM_15_FEATURES = feature_rankings.sort_values(by = 'average_score', ascending = False).iloc[0:15]

In [1]:

TOP_12_FEATURES_DF.index.to_list()

TOP_12_FEATURES = [
    'Curricular units 2nd sem (approved)',
    'Curricular units 1st sem (approved)',
    'Curricular units 2nd sem (grade)',
    'Tuition fees up to date',
    'Curricular units 1st sem (grade)',
    'Curricular units 2nd sem (evaluations)',
    'Curricular units 2nd sem (enrolled)',
    'Scholarship holder',
    'Curricular units 1st sem (evaluations)',
    'Course',
    'Curricular units 1st sem (enrolled)'
]

BOTTOM_15_FEATURES = [
    'International',
    'Educational special needs',
    'Nacionality',
    'Marital status',
    'Inflation rate',
    'Curricular units 1st sem (without evaluations)',
    'Father\'s qualification',
    'Mother\'s qualification',
    'Displaced',
    'Curricular units 2nd sem (credited)',
    'Curricular units 1st sem (credited)',
    'Application order',
    'Previous qualification',
    'Daytime/evening attendance',
    'Curricular units 2nd sem (without evaluations)'
]

NameError: name 'TOP_12_FEATURES_DF' is not defined

# Sequential Feature Selection

This was additional and wasn't included in the final feature selection

In [10]:
skfold = StratifiedKFold(n_splits = 5, shuffle=True, random_state=42)


sfs_backward = SFS(estimator = LGBMClassifier(random_state=42, 
                                            class_weight = 'balanced', 
                                            n_jobs = -1, 
                                            objective = 'multiclass'),
                                            k_features=(2, 3),
                                            forward=True,          # Set forward to False for backward selection
                                            floating=True,          # Set floating to True for floating selection
                                            verbose=0,
                                            scoring='f1_micro',
                                            cv = skfold
)

sfs_backward_pipeline = make_pipeline(
    initial_preprocess,
    sfs_backward
).fit(X,y)

selected_feature_indices = sfs_backward.k_feature_idx_
selected_features = initial_preprocess.get_feature_names_out()[list(selected_feature_indices)]
selected_features

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\model_selection\_validation.py:73: FutureWarning: `fit_params` is deprecated and will be removed in version 1.6. Pass parameters via `params` instead.
  warnings.warn(


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000091 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 90
[LightGBM] [Info] Number of data points in the train set: 61214, number of used features: 1
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000071 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 91
[LightGBM] [Info] Number of data points in the train set: 61214, number of used features: 1
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start traini

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\model_selection\_validation.py:73: FutureWarning: `fit_params` is deprecated and will be removed in version 1.6. Pass parameters via `params` instead.
  warnings.warn(


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000059 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 255
[LightGBM] [Info] Number of data points in the train set: 61214, number of used features: 1
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000173 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 255
[LightGBM] [Info] Number of data points in the train set: 61214, number of used features: 1
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Auto-choosing row-wi

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\model_selection\_validation.py:73: FutureWarning: `fit_params` is deprecated and will be removed in version 1.6. Pass parameters via `params` instead.
  warnings.warn(


...

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000159 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 23
[LightGBM] [Info] Number of data points in the train set: 61214, number of used features: 2
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits

c:\Users\Nebula PC\Desktop\Projects\Academic-Success-Prediction\.venv-academic-success\Lib\site-packages\sklearn\model_selection\_validation.py:73: FutureWarning: `fit_params` is deprecated and will be removed in version 1.6. Pass parameters via `params` instead.
  warnings.warn(


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000139 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 20
[LightGBM] [Info] Number of data points in the train set: 61214, number of used features: 2
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000165 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 20
[LightGBM] [Info] Number of data points in the train set: 61214, number of used features: 2
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start traini


[2024-06-25 14:09:38] Features: 3/3 -- score: 0.8005828141894422

array(['Curricular units 2nd sem (approved)', 'Course',
       'Tuition fees up to date'], dtype=object)

In [ ]:
# Print the selected feature indices
print("Selected feature indices:", sfs_backward.k_feature_idx_)

# Plot the sequential feature selection process
metric_dict = sfs_backward.get_metric_dict(confidence_interval=0.95)
fig = plot_sfs(metric_dict, kind='std_dev')

sfs_backward_pipeline.__dict__
plt.title('Sequential Floating Backward Selection (SFBS)')
plt.grid()
plt.show()
#
## Transform the training and testing data to the selected features
X_train_selected_features = sfs_backward.transform(X)
#X_test_selected_features = sfs_backward_pipeline.transform(X_test)
#
## Optionally, you can now train a model with the selected features
#model.fit(X_train_selected_features, y_train)
#accuracy = model.score(X_test_selected_features, y_test)
#print(f"Accuracy with selected features: {accuracy:.4f}")
X_train_selected_features